# This code helps you to parse data from НАШ.ДОМ.РФ web map

You can look at the map of new buildings [here](https://xn--80az8a.xn--d1aqf.xn--p1ai/%D1%81%D0%B5%D1%80%D0%B2%D0%B8%D1%81%D1%8B/%D0%BA%D0%B0%D1%82%D0%B0%D0%BB%D0%BE%D0%B3-%D0%BD%D0%BE%D0%B2%D0%BE%D1%81%D1%82%D1%80%D0%BE%D0%B5%D0%BA/%D1%81%D0%BF%D0%B8%D1%81%D0%BE%D0%BA-%D0%BE%D0%B1%D1%8A%D0%B5%D0%BA%D1%82%D0%BE%D0%B2/%D0%BA%D0%B0%D1%80%D1%82%D0%B0?bounds=-21.303352635369155%2C-60.46875099999995%2C84.10483966467523%2C179.99999900000003&objectIds=42470%2C41762%2C49513)

In [1]:
# Restart the kernel
import IPython
IPython.Application.instance().kernel.do_shutdown(True)
print('Ядро перезапущено, можно продолжать работать!')

Ядро перезапущено, можно продолжать работать!


### Import libraries


In [2]:
import pandas as pd
import geopandas as gpd

# For working with requests
import requests
import json

import folium
import matplotlib
import mapclassify

### Define bounding box (coordinates that limit search area)

In [3]:
latBounds = [56, 57]
longBounds = [60, 61]
bbbox = {'long': longBounds, 'lat': latBounds}

### URL API

In [4]:

base_url = "https://xn--80az8a.xn--d1aqf.xn--p1ai/%D1%81%D0%B5%D1%80%D0%B2%D0%B8%D1%81%D1%8B/api"
test_id = "40958"

url_get_points  = f"{base_url}/kn/object/map?offset=0&latitudePoint1=60&latitudePoin2=61&longitudePoint1=56&longitudePoint2=57"
url_get_point_info = f"{base_url}/object/{test_id}"

### Request list of available objects in a selected area

In [5]:
r = requests.get(url_get_points)
print(r.status_code)
data = r.json()

200


In [6]:
data

{'data': {'list': [{'objId': 43621,
    'objStatus': 2,
    'latitude': 54.4992,
    'longitude': 36.1909},
   {'objId': 48271, 'objStatus': 0, 'latitude': 53.1978, 'longitude': 45.2095},
   {'objId': 28589,
    'objStatus': 0,
    'latitude': 52.2241,
    'longitude': 104.2329},
   {'objId': 29375, 'objStatus': 2, 'latitude': 55.79, 'longitude': 37.5701},
   {'objId': 4097, 'objStatus': 2, 'latitude': 56.8995, 'longitude': 60.6243},
   {'objId': 44151, 'objStatus': 0, 'latitude': 55.7507, 'longitude': 37.4544},
   {'objId': 22107, 'objStatus': 2, 'latitude': 55.826, 'longitude': 37.1411},
   {'objId': 47823, 'objStatus': 0, 'latitude': 52.9484, 'longitude': 36.0329},
   {'objId': 17676, 'objStatus': 2, 'latitude': 64.5528, 'longitude': 40.5298},
   {'objId': 11815, 'objStatus': 2, 'latitude': 52.6013, 'longitude': 39.5099},
   {'objId': 42757,
    'objStatus': 0,
    'latitude': 48.4739,
    'longitude': 135.0859},
   {'objId': 40059,
    'objStatus': 2,
    'latitude': 46.9577,
    '

### Save objects IDs to an array

In [6]:
list_objects = data['data']['list']


# filtered_list_objects = [dict for dict in list_objects if dict['latitude'] ]
# objects_df = pd.DataFrame.from_dict(filtered_list_objects)
# objectsIds = [o['objId'] for o in filtered_list_objects if 'objId' in o]

objects_df = pd.DataFrame.from_dict(list_objects)
print(objects_df.head())

objectsIds = objects_df.loc[(  objects_df ['latitude'] <= 57 ) & ( objects_df ['latitude'] >= 56 )  & ( objects_df ['longitude'] >= 60 ) & ( objects_df ['longitude'] <= 61 )]['objId']
len(objectsIds)



   objId  objStatus  latitude  longitude
0  43621          2   54.4992    36.1909
1  48271          0   53.1978    45.2095
2  28589          0   52.2241   104.2329
3  29375          2   55.7900    37.5701
4   4097          2   56.8995    60.6243


854

### Function to GET properties for all objects

In [8]:
# def get_objects(bbox):
#     base_url = "https://xn--80az8a.xn--d1aqf.xn--p1ai/%D1%81%D0%B5%D1%80%D0%B2%D0%B8%D1%81%D1%8B/api"
#     url_get_points  = f"{base_url}/kn/object/map?offset=0&limit=999999&latitudePoint1={bbox['lat'][0]}&latitudePoin2={bbox['lat'][1]}&longitudePoint1={bbox['long'][0]}&longitudePoint2={bbox['long'][1]}"
#     r = requests.get(url_get_points)
#     listObjects = r.json()['data']['list']
#     objectsIds_all = [o['objId'] for o in listObjects if 'objId' in o]
#     objectsIds = objectsIds_all[0:100]
#     df_final = pd.DataFrame()

#     if r.status_code == 200:
#         for n, i in enumerate(objectsIds):
#             url_get_point_info = f"{base_url}/object/{i}"
#             r2 = requests.get(url_get_point_info)
#             if r2.status_code == 200:
#                 data = r2.json()['data']
#                 data_df = pd.DataFrame.from_dict([data])
#                 df_final = pd.concat([df_final, data_df], axis=0)
#             else:
#                 return r2.status_code
    
#     else:
#         return r.status_code

#     return  df_final


In [7]:
def get_objects(bbox):
    base_url = "https://xn--80az8a.xn--d1aqf.xn--p1ai/%D1%81%D0%B5%D1%80%D0%B2%D0%B8%D1%81%D1%8B/api"
    url_get_points  = f"{base_url}/kn/object/map?offset=0&latitudePoint1=60&latitudePoin2=61&longitudePoint1=56&longitudePoint2=57"
    r = requests.get(url_get_points)

    objects_df = pd.DataFrame.from_dict(list_objects)
    objectsIds = objects_df.loc[( objects_df ['latitude'] <= bbox['lat'][1] ) & ( objects_df ['latitude'] >= bbox['lat'][0] ) & ( objects_df ['longitude'] >= bbox['long'][0] ) & ( objects_df ['longitude'] <= bbox['long'][1])]['objId']
    df_final = pd.DataFrame()

    if r.status_code == 200:
        for n, i in enumerate(objectsIds):
            url_get_point_info = f"{base_url}/object/{i}"
            r2 = requests.get(url_get_point_info)
            if r2.status_code == 200:
                data = r2.json()['data']
                data_df = pd.DataFrame.from_dict([data])
                df_final = pd.concat([df_final, data_df], axis=0)
            else:
                continue

    
    else:
        return r.status_code

    return  df_final

In [8]:
objects = get_objects(bbbox)

In [9]:
objects

id  hobjId    pdId                                          developer  \
0    4097    7950    4952  {'devId': 1673, 'devShortCleanNm': 'ФОРМУЛА РА...   
0   16678   29496   33572  {'devId': 2698, 'devShortCleanNm': 'ЖИЛОЙ КОМП...   
0    5598    9704    6519  {'devId': 641, 'devShortCleanNm': 'БАШНЯ ВРЕМЕ...   
0   45859  126492  552140  {'devId': 13667, 'devShortCleanNm': 'СЗ НИЖНЕИ...   
0   21812   37258   22041  {'devId': 480, 'devShortCleanNm': 'ЮИТ УРАЛСТР...   
..    ...     ...     ...                                                ...   
0   41887  122422  473561  {'devId': 12816, 'devShortCleanNm': 'СЗ ТЕНИСТ...   
0    7467   22639   14336  {'devId': 1794, 'devShortCleanNm': 'СЗ СИК КАП...   
0   41065  121592  460324  {'devId': 12534, 'devShortCleanNm': 'СЗ АТОМ-С...   
0   16672   32655   33567  {'devId': 2697, 'devShortCleanNm': 'ОПТИМА', '...   
0   45173  125778  561234  {'devId': 10907, 'devShortCleanNm': 'СЗ ЖК ТЕМ...   

    region                                            address  floorMin  \
0       66  город Екатеринбург, переулок Цветочный, д. 16,...      12.0   
0       66  город Екатеринбург, улица Ясная - Шаумяна, бло...       1.0   
0       66  город Екатеринбург, район Железнодорожный, ули...       5.0   
0       66  г Екатеринбург, район Чкаловский р-н, квартал ...      29.0   
0       66             г Екатеринбург, пер Симбирский, д. 2/4      16.0   
..     ...                                                ...       ...   
0       66  г Екатеринбург, Верх-Исетский район, улица Тен...      10.0   
0       91  г Симферополь, район Железнодорожный, Улица Же...      11.0   
0       66                                     г Екатеринбург      10.0   
0       66                г Екатеринбург, ул Хохрякова, д. 63      13.0   
0       66  г Екатеринбург, ул 22 Партсъезда, строение 10,...      13.0   

    floorMax  objElemLivingCnt objReady100PercDt  ... objInfrstrTrashAreaCnt  \
0       16.0               203        2018-12-03  ...                    NaN   
0        1.0                 0        2016-02-01  ...                    NaN   
0       27.0               403        2018-12-29  ...                    NaN   
0       29.0               949        2024-09-30  ...                    2.0   
0       16.0               127        2018-12-24  ...                    NaN   
..       ...               ...               ...  ...                    ...   
0       10.0               106        2023-01-31  ...                    1.0   
0       11.0                98        2019-12-28  ...                    NaN   
0       10.0                56        2022-10-24  ...                    3.0   
0       32.0               230        2018-12-28  ...                    NaN   
0       23.0               258        2024-12-31  ...                    0.0   

   objInfrstrObjPrkngCnt objInfrstrNotObjPrkngCnt  objElevatorWheelchairCnt  \
0                    NaN                      NaN                       NaN   
0                    NaN                      NaN                       NaN   
0                    NaN                      NaN                       NaN   
0                    0.0                     29.0                       0.0   
0                    NaN                      NaN                       NaN   
..                   ...                      ...                       ...   
0                   25.0                      5.0                       0.0   
0                    NaN                      NaN                       NaN   
0                   88.0                      0.0                       0.0   
0                    NaN                      NaN                       NaN   
0                   35.0                      0.0                       0.0   

    objElevatorPassengerCnt objElevatorCargoCnt soldOutPerc objPriceAvg  \
0                       NaN                 NaN         NaN         NaN   
0                       NaN                 NaN         NaN         NaN   
0         

### Exporting data to a CSV file

In [46]:
objects.to_csv('./objects_ekat.csv', index=False, index_label=False)

### Creating Spatial Data Frame from a Data Frame

In [13]:
spatial = gpd.GeoDataFrame(objects, geometry=gpd.points_from_xy(objects.objLkLongitude, objects.objLkLatitude), crs='EPSG:4326')

### Explore the data 

In [15]:
spatial.explore()